In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

In [2]:
import pandas as pd
import datetime as dt
import pandas_profiling
import numpy as np
from matplotlib import pyplot as plt
import seaborn as sns
import warnings
warnings.filterwarnings("ignore")

#classification
from sklearn.naive_bayes import MultinomialNB,GaussianNB,BernoulliNB
from sklearn.neighbors import KNeighborsClassifier
from sklearn.svm import SVC
from sklearn.tree import DecisionTreeClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.ensemble import AdaBoostClassifier
from xgboost import XGBClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import classification_report, accuracy_score, confusion_matrix, precision_score, recall_score, f1_score
from sklearn.model_selection import train_test_split


/opt/conda/lib/python3.10/site-packages/numba/core/decorators.py:262: NumbaDeprecationWarning: numba.generated_jit is deprecated. Please see the documentation at: https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-generated-jit for more information and advice on a suitable replacement.
  warnings.warn(msg, NumbaDeprecationWarning)
/opt/conda/lib/python3.10/site-packages/visions/backends/shared/nan_handling.py:51: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  def hasna(x: np.ndarray) -> bool:
/tmp/ipykernel_32/611380139.py:3: DeprecationWarning: `import pandas_profiling` is going to be deprecated by April 1st. Please use `import ydata_profiling`

In [57]:
def classification_(x, y):
    g = GaussianNB()
    b = BernoulliNB()
    k = KNeighborsClassifier()
    svc = SVC()
    d = DecisionTreeClassifier()
    log = LogisticRegression()
    gbc = GradientBoostingClassifier()
    mn = MultinomialNB()
    rf = RandomForestClassifier()
    ab = AdaBoostClassifier()
    xgb = XGBClassifier()

    x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.2, random_state=42)

    top = (g, b, k, svc, d, log, gbc, mn, rf, ab, xgb)
    topname = ["GaussianNB", "BernoulliNB", "KNeighborsClassifier", "SVC", "DecisionTreeClassifier",
               "LogisticRegression", "GradientBoostingClassifier", "MultinomialNB", "RandomForestClassifier",
               "AdaBoostClassifier", "XGBClassifier"]

    accuracy = []
    precision = []
    recall = []
    f1 = []

    result = pd.DataFrame(columns=["AccuracyScore", "PrecisionScore", "RecallScore", "f1score"], index=topname)

    for i in top:
        rus = RandomUnderSampler(random_state=42)
        x_rus, y_rus = rus.fit_resample(x_train, y_train)
        predict = i.fit(x_rus, y_rus).predict(x_test)

        accuracy.append(accuracy_score(y_test, predict))
        precision.append(precision_score(y_test, predict))
        recall.append(recall_score(y_test, predict))
        f1.append(f1_score(y_test, predict))

    result.AccuracyScore = accuracy
    result.PrecisionScore = precision
    result.RecallScore = recall
    result.f1score = f1

    return result.sort_values("AccuracyScore", ascending=False)

In [6]:
data = pd.read_csv('../input/failuredata/failure.csv')

In [7]:
data.duplicated().sum()

0

In [8]:
data.isnull().sum()

date          0
device        0
failure       0
attribute1    0
attribute2    0
attribute3    0
attribute4    0
attribute5    0
attribute6    0
attribute7    0
attribute8    0
attribute9    0
dtype: int64

In [9]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 124494 entries, 0 to 124493
Data columns (total 12 columns):
 #   Column      Non-Null Count   Dtype 
---  ------      --------------   ----- 
 0   date        124494 non-null  object
 1   device      124494 non-null  object
 2   failure     124494 non-null  int64 
 3   attribute1  124494 non-null  int64 
 4   attribute2  124494 non-null  int64 
 5   attribute3  124494 non-null  int64 
 6   attribute4  124494 non-null  int64 
 7   attribute5  124494 non-null  int64 
 8   attribute6  124494 non-null  int64 
 9   attribute7  124494 non-null  int64 
 10  attribute8  124494 non-null  int64 
 11  attribute9  124494 non-null  int64 
dtypes: int64(10), object(2)
memory usage: 11.4+ MB


In [10]:
data.profile_report()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [12]:
data["date"]=pd.to_datetime(data["date"])

In [13]:
data["day"]=data["date"].dt.day
data["month"]=data["date"].dt.month
data["year"]=data["date"].dt.year

In [14]:
data


date    device  failure  attribute1  attribute2  attribute3  \
0      2015-01-01  S1F01085        0   215630672          56           0   
1      2015-01-01  S1F0166B        0    61370680           0           3   
2      2015-01-01  S1F01E6Y        0   173295968           0           0   
3      2015-01-01  S1F01JE0        0    79694024           0           0   
4      2015-01-01  S1F01R2B        0   135970480           0           0   
...           ...       ...      ...         ...         ...         ...   
124489 2015-11-02  Z1F0MA1S        0    18310224           0           0   
124490 2015-11-02  Z1F0Q8RT        0   172556680          96         107   
124491 2015-11-02  Z1F0QK05        0    19029120        4832           0   
124492 2015-11-02  Z1F0QL3N        0   226953408           0           0   
124493 2015-11-02  Z1F0QLC1        0    17572840           0           0   

        attribute4  attribute5  attribute6  attribute7  attribute8  \
0               52           6      407438           0           0   
1                0           6      403174           0           0   
2                0          12      237394           0           0   
3                0           6      410186           0           0   
4                0          15      313173           0           0   
...            ...         ...         ...         ...         ...   
124489           0          10      353705           8           8   
124490           4          11      332792           0           0   
124491           0          11      350410           0           0   
124492           0          12      358980           0           0   
124493           0          10      351431           0           0   

        attribute9  day  month  year  
0                7    1      1  2015  
1                0    1      1  2015  
2                0    1      1  2015  
3                0    1      1  2015  
4                3    1      1  2015  
...            ...  ...    ...   ...  
124489           0    2     11  2015  
124490          13    2     11  2015  
124491           0    2     11  2015  
124492           0    2     11  2015  
124493           0    2     11  2015  

[124494 rows x 15 columns]

In [15]:
data.failure.value_counts()
#---106 times, +++ 124388 times
#applied oversampling method to deal with unbalanced classification problem

0    124388
1       106
Name: failure, dtype: int64

In [18]:
data.nunique()

date             304
device          1168
failure            2
attribute1    123878
attribute2       558
attribute3        47
attribute4       115
attribute5        60
attribute6     44838
attribute7        28
attribute8        28
attribute9        65
day               31
month             11
year               1
dtype: int64

In [19]:
data.describe()

failure    attribute1     attribute2     attribute3  \
count  124494.000000  1.244940e+05  124494.000000  124494.000000   
mean        0.000851  1.223868e+08     159.484762       9.940455   
std         0.029167  7.045960e+07    2179.657730     185.747321   
min         0.000000  0.000000e+00       0.000000       0.000000   
25%         0.000000  6.127675e+07       0.000000       0.000000   
50%         0.000000  1.227957e+08       0.000000       0.000000   
75%         0.000000  1.833084e+08       0.000000       0.000000   
max         1.000000  2.441405e+08   64968.000000   24929.000000   

          attribute4     attribute5     attribute6     attribute7  \
count  124494.000000  124494.000000  124494.000000  124494.000000   
mean        1.741120      14.222693  260172.858025       0.292528   
std        22.908507      15.943021   99151.009852       7.436924   
min         0.000000       1.000000       8.000000       0.000000   
25%         0.000000       8.000000  221452.000000       0.000000   
50%         0.000000      10.000000  249799.500000       0.000000   
75%         0.000000      12.000000  310266.000000       0.000000   
max      1666.000000      98.000000  689161.000000     832.000000   

          attribute8     attribute9            day          month      year  
count  124494.000000  124494.000000  124494.000000  124494.000000  124494.0  
mean        0.292528      12.451524      14.894196       4.028299    2015.0  
std         7.436924     191.425623       8.759542       2.572167       0.0  
min         0.000000       0.000000       1.000000       1.000000    2015.0  
25%         0.000000       0.000000       7.000000       2.000000    2015.0  
50%         0.000000       0.000000      15.000000       3.000000    2015.0  
75%         0.000000       0.000000      22.000000       6.000000    2015.0  
max       832.000000   18701.000000      31.000000      11.000000    2015.0

In [20]:
data.corr()

failure  attribute1  attribute2  attribute3  attribute4  \
failure     1.000000    0.001984    0.052902   -0.000948    0.067398   
attribute1  0.001984    1.000000   -0.004248    0.003702    0.001837   
attribute2  0.052902   -0.004248    1.000000   -0.002617    0.146593   
attribute3 -0.000948    0.003702   -0.002617    1.000000    0.097452   
attribute4  0.067398    0.001837    0.146593    0.097452    1.000000   
attribute5  0.002270   -0.003370   -0.013999   -0.006696   -0.009773   
attribute6 -0.000550   -0.001516   -0.026350    0.009027    0.024870   
attribute7  0.119055    0.000151    0.141367   -0.001884    0.045631   
attribute8  0.119055    0.000151    0.141367   -0.001884    0.045631   
attribute9  0.001622    0.001122   -0.002736    0.532366    0.036069   
day         0.002994   -0.000239   -0.010000   -0.004232   -0.008383   
month       0.000321   -0.005613   -0.006416   -0.001101   -0.005490   
year             NaN         NaN         NaN         NaN         NaN   

            attribute5  attribute6  attribute7  attribute8  attribute9  \
failure       0.002270   -0.000550    0.119055    0.119055    0.001622   
attribute1   -0.003370   -0.001516    0.000151    0.000151    0.001122   
attribute2   -0.013999   -0.026350    0.141367    0.141367   -0.002736   
attribute3   -0.006696    0.009027   -0.001884   -0.001884    0.532366   
attribute4   -0.009773    0.024870    0.045631    0.045631    0.036069   
attribute5    1.000000   -0.017051   -0.009384   -0.009384    0.005949   
attribute6   -0.017051    1.000000   -0.012207   -0.012207    0.021152   
attribute7   -0.009384   -0.012207    1.000000    1.000000    0.006861   
attribute8   -0.009384   -0.012207    1.000000    1.000000    0.006861   
attribute9    0.005949    0.021152    0.006861    0.006861    1.000000   
day           0.009526    0.019483    0.009194    0.009194   -0.012316   
month        -0.014129    0.138159    0.020576    0.020576   -0.025383   
year               NaN         NaN         NaN         NaN         NaN   

                 day     month  year  
failure     0.002994  0.000321   NaN  
attribute1 -0.000239 -0.005613   NaN  
attribute2 -0.010000 -0.006416   NaN  
attribute3 -0.004232 -0.001101   NaN  
attribute4 -0.008383 -0.005490   NaN  
attribute5  0.009526 -0.014129   NaN  
attribute6  0.019483  0.138159   NaN  
attribute7  0.009194  0.020576   NaN  
attribute8  0.009194  0.020576   NaN  
attribute9 -0.012316 -0.025383   NaN  
day         1.000000  0.008209   NaN  
month       0.008209  1.000000   NaN  
year             NaN       NaN   NaN

In [21]:
data.corr()["failure"].sort_values(ascending=False)
#look at attribute 8,7

failure       1.000000
attribute7    0.119055
attribute8    0.119055
attribute4    0.067398
attribute2    0.052902
day           0.002994
attribute5    0.002270
attribute1    0.001984
attribute9    0.001622
month         0.000321
attribute6   -0.000550
attribute3   -0.000948
year               NaN
Name: failure, dtype: float64

In [22]:
del data["attribute8"]

In [43]:
del data["date"]

In [44]:
data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 106351 entries, 1 to 124493
Data columns (total 13 columns):
 #   Column      Non-Null Count   Dtype 
---  ------      --------------   ----- 
 0   device      106351 non-null  object
 1   failure     106351 non-null  int64 
 2   attribute1  106351 non-null  int64 
 3   attribute2  106351 non-null  int64 
 4   attribute3  106351 non-null  object
 5   attribute4  106351 non-null  object
 6   attribute5  106351 non-null  int64 
 7   attribute6  106351 non-null  int64 
 8   attribute7  106351 non-null  object
 9   attribute9  106351 non-null  object
 10  day         106351 non-null  int64 
 11  month       106351 non-null  int64 
 12  year        106351 non-null  int64 
dtypes: int64(8), object(5)
memory usage: 11.4+ MB


In [45]:
data["device"]=[i[:4] for i in data.device.values.tolist()]

In [46]:
data.device.value_counts()

S1F0    29079
S1F1    19916
W1F0    19782
W1F1    17124
Z1F0    13725
Z1F1     6490
Z1F2      235
Name: device, dtype: int64

In [47]:
x=data.drop("failure",axis=1)
y=data["failure"]

In [48]:
data[["attribute3","attribute4","attribute7","attribute9"]]=data[["attribute3","attribute4","attribute7","attribute9"]].astype("object")

In [49]:
outliers=data.quantile(.95)
data=data[(data["attribute1"]<outliers["attribute1"])]
data=data[(data["attribute2"]<outliers["attribute2"])]
data=data[(data["attribute6"]<outliers["attribute6"])]


In [50]:
x=pd.get_dummies(x,drop_first=True)

In [51]:
from imblearn.under_sampling import RandomUnderSampler
from imblearn.metrics import geometric_mean_score, make_index_balanced_accuracy, classification_report_imbalanced
from sklearn.metrics import confusion_matrix

In [52]:
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.2, random_state=42)
gbc = GradientBoostingClassifier()


In [53]:
rus = RandomUnderSampler(random_state=42)
x_rus, y_rus = rus.fit_resample(x_train, y_train)
predict = gbc.fit(x_rus, y_rus).predict(x_test)

In [55]:
confusion_matrix(y_test,predict)

array([[11799,  9459],
       [    2,    11]])

In [58]:
classification_(x,y)

AccuracyScore  PrecisionScore  RecallScore  \
BernoulliNB                      0.951577        0.002933     0.230769   
RandomForestClassifier           0.775187        0.001672     0.615385   
DecisionTreeClassifier           0.554934        0.000950     0.692308   
AdaBoostClassifier               0.551831        0.001153     0.846154   
GradientBoostingClassifier       0.538198        0.001119     0.846154   
XGBClassifier                    0.538009        0.000915     0.692308   
MultinomialNB                    0.532744        0.000704     0.538462   
KNeighborsClassifier             0.498378        0.000843     0.692308   
SVC                              0.374924        0.000602     0.615385   
GaussianNB                       0.316064        0.000756     0.846154   
LogisticRegression               0.305533        0.000677     0.769231   

                             f1score  
BernoulliNB                 0.005792  
RandomForestClassifier      0.003335  
DecisionTreeClassifier      0.001898  
AdaBoostClassifier          0.002302  
GradientBoostingClassifier  0.002235  
XGBClassifier               0.001828  
MultinomialNB               0.001407  
KNeighborsClassifier        0.001684  
SVC                         0.001202  
GaussianNB                  0.001510  
LogisticRegression          0.001352

In [60]:
import tensorflow as tf

In [62]:
model = tf.keras.Sequential([
                             tf.keras.layers.Dense(512, activation="relu"),
                             tf.keras.layers.Dense(512, activation="relu"),
                             tf.keras.layers.Dropout(0.25),
                             tf.keras.layers.Flatten(),
                             tf.keras.layers.Dense(512, activation="relu"),
                             tf.keras.layers.Dropout(0.50),
                             tf.keras.layers.Dense(512, activation="relu"),
                             tf.keras.layers.Dense(512, activation="softmax"),])

model.compile(optimizer="adam",
             loss=tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True),
             metrics=["accuracy"])
history=model.fit(x_rus,y_rus, batch_size=128, epochs=40, verbose=1, validation_data=(x_test,y_test))

Epoch 1/40
1/1 [==============================] - 4s 4s/step - loss: 9555548.0000 - accuracy: 0.0000e+00 - val_loss: 319.3599 - val_accuracy: 0.9961
Epoch 2/40
1/1 [==============================] - 1s 1s/step - loss: 867597.5625 - accuracy: 0.5541 - val_loss: 4829589.0000 - val_accuracy: 6.1116e-04
Epoch 3/40
1/1 [==============================] - 1s 1s/step - loss: 1892621.0000 - accuracy: 0.5135 - val_loss: 834.6033 - val_accuracy: 0.9987
Epoch 4/40
1/1 [==============================] - 3s 3s/step - loss: 1030921.7500 - accuracy: 0.5946 - val_loss: 650.9235 - val_accuracy: 0.9986
Epoch 5/40
1/1 [==============================] - 1s 1s/step - loss: 875289.3125 - accuracy: 0.5676 - val_loss: 411847.9688 - val_accuracy: 6.1116e-04
Epoch 6/40
1/1 [==============================] - 1s 1s/step - loss: 1033021.5000 - accuracy: 0.4595 - val_loss: 178.6036 - val_accuracy: 0.9984
Epoch 7/40
1/1 [==============================] - 1s 1s/step - loss: 761348.6250 - accuracy: 0.5405 - val_loss: 1

In [63]:
_,accuracy=model.evaluate(x_test,y_test)
print("Accuracy: %2f" % (accuracy*100))

665/665 [==============================] - 3s 5ms/step - loss: 138.3551 - accuracy: 0.9974
Accuracy: 99.741429
